In [0]:
jdbcHostname = "server4traffic.database.windows.net"
jdbcDatabase = "datawarehouse04"
jdbcPort = 1433
jdbcUsername = "admin2traffic"
jdbcPassword = "abcd1234@"

In [0]:
# URL JDBC
jdbcUrl = f"jdbc:sqlserver://{jdbcHostname}:{jdbcPort};database={jdbcDatabase};encrypt=true;trustServerCertificate=false;hostNameInCertificate=*.database.windows.net;loginTimeout=30;"

# Paramètres de connexion
connectionProperties = {
  "user" : jdbcUsername,
  "password" : jdbcPassword,
  "driver" : "com.microsoft.sqlserver.jdbc.SQLServerDriver"
}

In [0]:
import pyspark.sql.functions as F
from pyspark.sql.types import TimestampType


In [0]:
dbutils.widgets.text("date_param", "")
date_a_traiter = dbutils.widgets.get("date_param")

In [0]:
# construire la requête SQL avec filtre
query = f"(SELECT * FROM raw.transactions WHERE CAST(timestamp_insertion AS DATE) = '{date_a_traiter}') AS transactions_filtrés"

# lire uniquement les données de la veille
df_transactions = spark.read.jdbc(
    url=jdbcUrl,
    table=query,
    properties=connectionProperties
)

In [0]:
# # Lire une table SQL dans un DataFrame Spark
# df_transactions = spark.read.jdbc(url=jdbcUrl, table="raw.transactions", properties=connectionProperties)

In [0]:
display(df_transactions.limit(10))

store_id date heure transactions chiffre_affaires 1 2023-04-27 00:00:00 0.0 0.0 1 2023-04-27 01:00:00 0.0 0.0 1 2023-04-27 02:00:00 0.0 0.0 1 2023-04-27 03:00:00 0.0 0.0 1 2023-04-27 04:00:00 0.0 0.0 1 2023-04-27 05:00:00 0.0 0.0 1 2023-04-27 06:00:00 0.0 0.0 1 2023-04-27 07:00:00 0.0 0.0 1 2023-04-27 08:00:00 0.0 0.0 1 2023-04-27 09:00:00 56.0 3478.81

In [0]:
# Compter les lignes où AU MOINS UNE colonne est null
nb_lignes_null = df_transactions.filter(
    F.col("store_id").isNull() |
    F.col("date").isNull() |
    F.col("heure").isNull() |
    F.col("transactions").isNull() |
    F.col("chiffre_affaires").isNull()
).count()

In [0]:
print(f"Nombre de lignes avec au moins un null : {nb_lignes_null}")

Nombre de lignes avec au moins un null : 1209


In [0]:
df_transactions = df_transactions.dropna()


In [0]:
clean_transactions = df_transactions.withColumn(
    "date", F.coalesce(
        F.to_date("date", "yyyy-MM-dd"),
        F.to_date("date", "yyyy/MM/dd"),
        F.to_date("date", "dd/MM/yyyy")
    )
).withColumn(
    "store_id", F.col("store_id").cast("int")
).withColumn(
    "heure", F.hour(F.col("heure").cast(TimestampType()))
).withColumn(
    "nb_transactions", F.col("transactions").cast("int")
).withColumn(
    "chiffre_affaires", F.round(F.col("chiffre_affaires").cast("double"), 2)
).select(
    "store_id", "date", "heure", "nb_transactions", "chiffre_affaires"
)
display(clean_transactions)

store_id date heure nb_transactions chiffre_affaires 1 2023-04-27 0 0 0.0 1 2023-04-27 1 0 0.0 1 2023-04-27 2 0 0.0 1 2023-04-27 3 0 0.0 1 2023-04-27 4 0 0.0 1 2023-04-27 5 0 0.0 1 2023-04-27 6 0 0.0 1 2023-04-27 7 0 0.0 1 2023-04-27 8 0 0.0 1 2023-04-27 9 56 3478.81 1 2023-04-27 10 119 7844.15 1 2023-04-27 11 96 6008.11 1 2023-04-27 12 120 7132.01 1 2023-04-27 13 133 9165.67 1 2023-04-27 14 103 6709.42 1 2023-04-27 15 132 8808.94 1 2023-04-27 16 110 7025.82 1 2023-04-27 17 209 13592.59 1 2023-04-27 18 189 12221.38 1 2023-04-27 19 105 6327.85 1 2023-04-27 20 0 0.0 1 2023-04-27 21 0 0.0 1 2023-04-27 0 0 0.0 1 2023-04-27 23 0 0.0 2 2023-04-27 0 0 0.0 2 2023-04-27 1 0 0.0 2 2023-04-27 2 0 0.0 2 2023-04-27 3 0 0.0 2 2023-04-27 4 0 0.0 2 2023-04-27 5 0 0.0 2 2023-04-27 6 0 0.0 2 2023-04-27 7 0 0.0 2 2023-04-27 8 0 0.0 2 2023-04-27 9 53 3294.15 2 2023-04-27 10 82 5162.96 2 2023-04-27 11 83 5333.42 2 2023-04-27 12 112 6959.74 2 2023-04-27 13 178 11308.46 2 2023-04-27 14 55 3441.41 2 2023-04-27 15 82 5113.54 2 2023-04-27 16 80 4483.64 2 2023-04-27 17 83 5474.97 2 2023-04-27 18 125 7986.04 2 2023-04-27 19 79 4758.2 2 2023-04-27 20 0 0.0 2 2023-04-27 21 0 0.0 2 2023-04-27 22 0 0.0 2 2023-04-27 23 0 0.0 3 2023-04-27 0 0 0.0 3 2023-04-27 1 0 0.0 3 2023-04-27 2 0 0.0 3 2023-04-27 3 0 0.0 3 2023-04-27 4 0 0.0 898 2023-04-27 5 0 0.0 3 2023-04-27 6 0 0.0 3 2023-04-27 7 0 0.0 3 2023-04-27 8 0 0.0 3 2023-04-27 9 53 3696.18 3 2023-04-27 10 85 6390.41 3 2023-04-27 11 65 4404.99 3 2023-04-27 12 137 9120.85 3 2023-04-27 13 89 6086.5 3 2023-04-27 14 97 6194.53 3 2023-04-27 15 61 4338.46 3 2023-04-27 16 59 3558.34 3 2023-04-27 17 154 9691.09 3 2023-04-27 18 137 9158.88 3 2023-04-27 19 109 6943.91 3 2023-04-27 20 0 0.0 3 2023-04-27 21 0 0.0 3 2023-04-27 22 0 0.0 4 2023-04-27 0 0 0.0 4 2023-04-27 1 0 0.0 898 2023-04-27 2 0 0.0 4 2023-04-27 3 0 0.0 4 2023-04-27 4 0 0.0 4 2023-04-27 5 0 0.0 4 2023-04-27 6 0 0.0 4 2023-04-27 7 0 0.0 4 2023-04-27 8 0 0.0 4 2023-04-27 9 31 1664.12 4 2023-04-27 10 41 2410.3 4 2023-04-27 11 97 6289.23 4 2023-04-27 12 88 5773.27 4 2023-04-27 13 67 4259.09 4 2023-04-27 14 57 3578.74 4 2023-04-27 15 88 5212.71 4 2023-04-27 16 54 3572.5 4 2023-04-27 17 105 6642.34 4 2023-04-27 18 109 6944.19 4 2023-04-27 19 68 4630.71 4 2023-04-27 20 0 0.0 4 2023-04-27 21 0 0.0 4 2023-04-27 22 0 0.0 4 2023-04-27 23 0 0.0 5 2023-04-27 0 0 0.0 5 2023-04-27 1 0 0.0 5 2023-04-27 2 0 0.0 5 2023-04-27 3 0 0.0 5 2023-04-27 4 0 0.0 5 2023-04-27 5 0 0.0 5 2023-04-27 6 0 0.0 5 2023-04-27 7 0 0.0 5 2023-04-27 8 0 0.0 5 2023-04-27 9 33 1921.21 5 2023-04-27 10 34 1969.28 5 2023-04-27 11 48 2674.76 5 2023-04-27 12 83 5167.58 5 2023-04-27 13 65 4073.44 5 2023-04-27 14 45 2905.5 5 2023-04-27 15 48 2934.25 5 2023-04-27 16 46 2990.45 5 2023-04-27 18 49 3339.39 5 2023-04-27 19 50 2898.68 5 2023-04-27 20 0 0.0 5 2023-04-27 21 0 0.0 5 2023-04-27 22 0 0.0 5 2023-04-27 23 0 0.0 6 2023-04-27 0 0 0.0 6 2023-04-27 1 0 0.0 6 2023-04-27 2 0 0.0 6 2023-04-27 3 0 0.0 6 2023-04-27 4 0 0.0 6 2023-04-27 5 0 0.0 6 2023-04-27 6 0 0.0 6 2023-04-27 7 0 0.0 6 2023-04-27 8 0 0.0 6 2023-04-27 9 28 1530.51 6 2023-04-27 10 33 2150.68 6 2023-04-27 11 36 999999.99 6 2023-04-27 12 40 2601.62 6 2023-04-27 13 58 3646.36 6 2023-04-27 14 60 3902.53 6 2023-04-27 15 30 2161.66 6 2023-04-27 16 50 3351.17 6 2023-04-27 17 67 4625.02 6 2023-04-27 18 49 3423.9 6 2023-04-27 19 50 3286.81 6 2023-04-27 20 0 0.0 6 2023-04-27 21 0 0.0 6 2023-04-27 22 0 0.0 6 2023-04-27 23 0 0.0 7 2023-04-27 0 0 0.0 7 2023-04-27 1 0 0.0 7 2023-04-27 2 0 0.0 7 2023-04-27 3 0 0.0 7 2023-04-27 4 0 0.0 7 2023-04-27 5 0 0.0 7 2023-04-27 6 0 0.0 7 2023-04-27 7 0 0.0 7 2023-04-27 8 0 0.0 7 2023-04-27 9 37 2117.83 7 2023-04-27 10 51 3218.84 7 2023-04-27 11 67 4645.76 7 2023-04-27 12 79 5473.61 7 2023-04-27 0 99 6261.14 7 2023-04-27 14 57 3396.77 7 2023-04-27 15 72 4902.3 7 2023-04-27 16 50 3354.87 7 2023-04-27 17 66 4311.15 7 2023-04-27 18 113 7828.33 7 2023-04-27 19 54 3183.63 7 2023-04-27 20 0 0.0 7 2023-04-27 21 0 0.0 7 2023-04-

In [0]:
clean_transactions.createOrReplaceTempView("clean_transactions")

In [0]:
spark.sql("""
    SELECT 
        *
    FROM clean_transactions
    where nb_transactions> 1000
    ORDER BY nb_transactions
""").show(10)

+--------+----------+-----+---------------+----------------+
|store_id|      date|heure|nb_transactions|chiffre_affaires|
+--------+----------+-----+---------------+----------------+
|       5|2023-05-11|    2|           9999|             0.0|
|       8|2023-05-05|   20|           9999|             0.0|
|       1|2023-05-01|    5|           9999|             0.0|
|       7|2023-05-03|    6|           9999|             0.0|
|      10|2023-05-09|   15|           9999|         1726.42|
|       4|2023-05-01|   10|           9999|         2505.48|
|      10|2023-05-15|   10|           9999|         1002.91|
|       4|2023-05-15|   22|           9999|             0.0|
|       3|2023-05-11|   11|           9999|         3941.03|
|       8|2023-05-04|   18|           9999|         5099.83|
+--------+----------+-----+---------------+----------------+
only showing top 10 rows



In [0]:
# Filtrage des données
clean_transactions = clean_transactions.filter(
    (F.col("store_id") <= 10) &
    (F.col("heure").between(9, 19)) &
    (F.col("date").isNotNull()) &
    (F.col("nb_transactions").between(1, 1000)) &
    (F.col("chiffre_affaires").between(1, 50000))
)
clean_transactions.createOrReplaceTempView("clean_transactions")

display(clean_transactions)

store_id date heure nb_transactions chiffre_affaires 1 2023-04-27 9 56 3478.81 1 2023-04-27 10 119 7844.15 1 2023-04-27 11 96 6008.11 1 2023-04-27 12 120 7132.01 1 2023-04-27 13 133 9165.67 1 2023-04-27 14 103 6709.42 1 2023-04-27 15 132 8808.94 1 2023-04-27 16 110 7025.82 1 2023-04-27 17 209 13592.59 1 2023-04-27 18 189 12221.38 1 2023-04-27 19 105 6327.85 2 2023-04-27 9 53 3294.15 2 2023-04-27 10 82 5162.96 2 2023-04-27 11 83 5333.42 2 2023-04-27 12 112 6959.74 2 2023-04-27 13 178 11308.46 2 2023-04-27 14 55 3441.41 2 2023-04-27 15 82 5113.54 2 2023-04-27 16 80 4483.64 2 2023-04-27 17 83 5474.97 2 2023-04-27 18 125 7986.04 2 2023-04-27 19 79 4758.2 3 2023-04-27 9 53 3696.18 3 2023-04-27 10 85 6390.41 3 2023-04-27 11 65 4404.99 3 2023-04-27 12 137 9120.85 3 2023-04-27 13 89 6086.5 3 2023-04-27 14 97 6194.53 3 2023-04-27 15 61 4338.46 3 2023-04-27 16 59 3558.34 3 2023-04-27 17 154 9691.09 3 2023-04-27 18 137 9158.88 3 2023-04-27 19 109 6943.91 4 2023-04-27 9 31 1664.12 4 2023-04-27 10 41 2410.3 4 2023-04-27 11 97 6289.23 4 2023-04-27 12 88 5773.27 4 2023-04-27 13 67 4259.09 4 2023-04-27 14 57 3578.74 4 2023-04-27 15 88 5212.71 4 2023-04-27 16 54 3572.5 4 2023-04-27 17 105 6642.34 4 2023-04-27 18 109 6944.19 4 2023-04-27 19 68 4630.71 5 2023-04-27 9 33 1921.21 5 2023-04-27 10 34 1969.28 5 2023-04-27 11 48 2674.76 5 2023-04-27 12 83 5167.58 5 2023-04-27 13 65 4073.44 5 2023-04-27 14 45 2905.5 5 2023-04-27 15 48 2934.25 5 2023-04-27 16 46 2990.45 5 2023-04-27 18 49 3339.39 5 2023-04-27 19 50 2898.68 6 2023-04-27 9 28 1530.51 6 2023-04-27 10 33 2150.68 6 2023-04-27 12 40 2601.62 6 2023-04-27 13 58 3646.36 6 2023-04-27 14 60 3902.53 6 2023-04-27 15 30 2161.66 6 2023-04-27 16 50 3351.17 6 2023-04-27 17 67 4625.02 6 2023-04-27 18 49 3423.9 6 2023-04-27 19 50 3286.81 7 2023-04-27 9 37 2117.83 7 2023-04-27 10 51 3218.84 7 2023-04-27 11 67 4645.76 7 2023-04-27 12 79 5473.61 7 2023-04-27 14 57 3396.77 7 2023-04-27 15 72 4902.3 7 2023-04-27 16 50 3354.87 7 2023-04-27 17 66 4311.15 7 2023-04-27 18 113 7828.33 7 2023-04-27 19 54 3183.63 8 2023-04-27 9 20 1246.75 8 2023-04-27 11 38 2551.27 8 2023-04-27 12 69 4415.05 8 2023-04-27 13 88 5364.37 8 2023-04-27 14 39 2690.41 8 2023-04-27 15 58 3697.9 8 2023-04-27 16 35 2019.54 8 2023-04-27 17 76 5057.68 8 2023-04-27 18 51 2781.84 8 2023-04-27 19 46 2973.9 9 2023-04-27 9 38 2708.14 9 2023-04-27 10 35 2244.05 9 2023-04-27 11 35 2212.81 9 2023-04-27 12 40 2780.65 9 2023-04-27 13 51 3467.94 9 2023-04-27 14 42 2499.23 9 2023-04-27 15 55 3329.12 9 2023-04-27 16 36 2338.0 9 2023-04-27 17 89 6080.72 9 2023-04-27 18 60 4200.81 9 2023-04-27 19 89 5673.91 10 2023-04-27 9 14 1047.12 10 2023-04-27 10 28 1660.19 10 2023-04-27 11 41 2674.51 10 2023-04-27 12 24 1748.81 10 2023-04-27 13 56 3394.05 10 2023-04-27 14 35 2399.61 10 2023-04-27 15 33 2251.65 10 2023-04-27 16 28 1785.56 10 2023-04-27 17 37 2482.18 10 2023-04-27 18 55 3047.81 10 2023-04-27 19 43 2713.68 1 2023-04-28 9 80 5288.72 1 2023-04-28 10 84 5344.28 1 2023-04-28 11 131 8502.0 1 2023-04-28 12 171 11308.59 1 2023-04-28 13 220 14424.36 1 2023-04-28 14 202 12922.39 1 2023-04-28 15 138 8524.39 1 2023-04-28 17 237 15273.17 1 2023-04-28 18 195 12665.84 1 2023-04-28 19 133 8821.55 2 2023-04-28 10 89 5680.18 2 2023-04-28 11 126 7683.89 2 2023-04-28 12 107 7045.7 2 2023-04-28 13 97 6918.34 2 2023-04-28 14 115 7683.44 2 2023-04-28 15 122 7452.35 2 2023-04-28 16 68 4354.6 2 2023-04-28 17 171 10354.01 2 2023-04-28 19 109 7067.31 3 2023-04-28 9 62 4195.09 3 2023-04-28 10 103 6369.3 3 2023-04-28 11 120 8129.41 3 2023-04-28 12 151 9547.66 3 2023-04-28 13 163 10145.82 3 2023-04-28 14 142 8870.33 3 2023-04-28 15 86 5755.88 3 2023-04-28 16 102 7463.63 3 2023-04-28 17 110 7223.91 3 2023-04-28 18 240 16099.23 3 2023-04-28 19 154 10149.61 4 2023-04-28 9 45 2879.75 4 2023-04-28 10 91 5764.92 4 2023-04-28 11 55 3555.61 4 2023-04-28 12 136 9186.92 4 2023-04-28 13 116 8385.64 4 2023-04-28 14 94 6191.96 4 2023-04-28 15 62 3903.92 4 2023-04-28 16 56 3294.15 4 2023-04-28 17 107

In [0]:
transactions_manquants = spark.sql("""
    -- table des dates attendues
    WITH heures_attendues AS (
        SELECT explode(sequence(9, 19)) AS heure
    ), 
    dates_attendues AS (
        select d.date from
        (SELECT explode(sequence(DATE '2023-04-27', DATE '2025-04-25', 
        INTERVAL 1 DAY)
        ) AS date) as d
        where dayofweek(d.date) BETWEEN 2 AND 6
    ),
    -- ids des magasins et des capteurs
    identifiants_uniques AS (
        SELECT DISTINCT store_id
        FROM clean_transactions
    ),
    toutes_combinaisons AS (
        SELECT i.store_id, d.date, h.heure
        FROM identifiants_uniques i
        CROSS JOIN dates_attendues d
        CROSS JOIN heures_attendues h
    )

    select t.store_id, t.date,t.heure
    from toutes_combinaisons t
    left join clean_transactions v
    on v.store_id = t.store_id
    and v.date = t.date
    and v.heure = t.heure
    where v.heure is null

""")
transactions_manquants.createOrReplaceTempView("transactions_manquants")
display(transactions_manquants)



store_id date heure 1 2023-08-29 15 2 2023-09-21 18 2 2023-10-23 12 1 2024-01-03 11 5 2024-01-09 9 10 2024-08-13 15 7 2025-01-29 15 7 2025-03-18 15 5 2025-03-14 15 10 2023-08-25 10 8 2023-11-08 12 7 2024-01-08 18 4 2024-02-05 19 1 2024-02-02 13 3 2024-04-17 10 9 2024-08-06 19 8 2024-11-04 18 2 2023-06-23 18 9 2023-10-06 11 8 2024-04-16 13 6 2024-07-30 12 7 2024-08-12 9 5 2024-11-08 12 10 2024-11-25 9 1 2025-03-28 14 4 2023-08-10 15 5 2024-01-25 17 4 2024-03-29 11 1 2024-05-10 14 3 2024-07-24 13 7 2024-09-30 17 8 2024-11-01 17 1 2024-11-22 12 8 2024-12-11 18 6 2023-06-08 11 10 2023-11-20 13 6 2024-02-08 12 4 2024-03-22 17 2 2024-05-27 13 8 2024-07-16 13 9 2024-10-15 12 1 2024-11-05 18 5 2024-12-24 15 2 2025-03-11 16 7 2025-04-25 11 5 2023-05-05 18 9 2023-05-31 13 2 2023-08-15 10 4 2023-09-01 14 2 2023-10-17 19 10 2023-10-20 19 10 2023-12-20 12 1 2024-03-11 13 6 2024-05-03 19 1 2024-06-19 16 3 2024-09-13 18 8 2024-10-25 10 1 2024-12-19 15 8 2025-03-03 16 1 2025-03-19 15 5 2023-08-18 12 3 2023-09-25 18 1 2023-10-31 18 5 2024-01-25 12 8 2024-04-03 15 3 2024-04-19 15 3 2024-04-19 16 1 2024-07-11 9 5 2024-08-27 18 6 2024-09-25 16 5 2024-11-14 13 10 2025-01-30 15 9 2025-04-04 9 10 2023-08-22 10 8 2023-11-24 13 8 2024-01-10 13 5 2024-06-20 14 1 2024-07-18 12 4 2024-08-06 14 1 2024-08-02 17 6 2024-12-27 15 8 2025-02-03 9 1 2025-04-14 11 3 2023-05-04 19 6 2023-05-04 10 8 2023-05-26 18 1 2023-06-01 14 10 2023-10-11 9 1 2023-12-14 18 6 2024-02-21 17 9 2024-04-03 10 4 2024-08-13 15 3 2024-08-22 16 4 2024-10-02 17 10 2024-12-23 9 1 2025-03-24 12 10 2024-03-01 13 4 2024-05-22 18 5 2024-07-24 18 10 2024-10-17 17 1 2024-11-14 14 6 2025-02-27 15 5 2025-03-04 11 5 2025-03-20 18 9 2023-05-08 10 9 2023-05-16 13 10 2023-06-21 11 4 2023-06-21 9 8 2023-06-27 12 5 2023-07-18 13 5 2023-07-24 17 5 2023-08-07 18 10 2023-08-16 16 1 2024-02-08 19 2 2024-03-21 18 10 2024-03-29 17 8 2024-06-27 17 7 2024-11-28 18 3 2024-12-26 19 9 2025-02-26 12 10 2025-03-13 15 10 2023-06-28 17 8 2023-06-28 16 3 2023-08-11 13 7 2023-08-18 19 10 2023-08-24 19 8 2024-01-02 11 5 2024-02-02 15 8 2024-05-13 11 3 2024-06-20 15 7 2023-07-21 18 5 2023-08-30 12 8 2023-09-21 9 8 2023-09-25 11 4 2023-10-04 18 3 2024-01-25 13 10 2024-02-06 17 7 2024-05-27 15 3 2024-05-27 18 2 2024-06-12 17 7 2024-06-14 16 6 2024-09-16 12 9 2025-01-22 16 7 2023-06-06 11 7 2023-09-11 13 3 2023-09-19 12 10 2023-11-08 10 1 2024-02-12 12 6 2024-07-12 13 1 2025-01-09 18 1 2025-02-20 17 1 2023-06-14 17 10 2023-12-15 9 4 2024-03-01 19 1 2024-03-26 9 3 2024-07-17 14 5 2024-09-18 10 7 2024-10-02 17 10 2024-11-29 16 9 2024-12-06 18 6 2025-02-05 19 7 2023-05-30 13 5 2023-07-03 19 4 2023-07-21 9 10 2023-08-14 9 6 2024-01-16 18 9 2024-05-17 12 4 2024-09-19 18 1 2025-04-01 18 8 2023-05-05 12 10 2023-06-13 15 5 2023-06-19 17 2 2023-07-18 11 6 2023-08-10 16 1 2023-11-10 10 10 2023-11-22 16 1 2024-01-05 18 5 2024-01-10 11 8 2024-07-31 16 9 2024-10-03 17 1 2024-11-27 14 3 2024-12-03 11 3 2024-12-09 10 7 2025-03-03 17 5 2025-04-08 16 8 2023-08-14 16 8 2023-10-26 17 1 2023-11-14 15 3 2023-11-22 14 3 2023-11-28 12 6 2024-04-24 16 2 2024-06-13 12 2 2024-12-04 17 4 2024-12-17 15 9 2025-04-08 15 7 2023-08-01 19 4 2023-09-20 10 5 2023-10-04 15 10 2023-10-31 14 9 2024-01-11 14 9 2024-07-08 13 1 2024-07-25 10 2 2024-12-04 12 10 2025-03-19 15 4 2023-05-22 13 4 2023-08-08 11 8 2023-11-24 10 10 2024-02-07 16 9 2024-03-12 15 7 2024-03-26 16 4 2024-04-19 12 1 2024-04-19 15 3 2024-08-27 11 8 2024-11-11 10 7 2025-02-13 16 4 2025-03-11 19 9 2025-04-08 10 6 2023-05-31 16 4 2023-07-26 12 9 2024-01-15 10 9 2024-10-07 9 7 2024-10-21 14 5 2024-12-05 13 1 2024-12-18 18 2 2025-02-14 15 8 2025-04-14 19 4 2025-04-17 13 2 2023-05-11 17 8 2023-09-26 11 3 2023-11-16 19 3 2023-11-29 14 3 2024-03-27 14 8 2024-05-29 9 3 2024-06-07 11 4 2025-01-17 10 9 2025-04-15 10 8 2023-06-30 18 8 2023-07-11 11 3 2023-08-07 14 2 2023-11-23 15 7 2024-03-12 11 2 2024-08-08 15 9 2024-08-12 13 10 2024-09-20 9 1 2024-10-10 14 2 2024-12-16 14 5 2024-12-11 18 9 2025-02-03 16 

In [0]:
transactions_manquants = spark.sql("""
    with moyenne_transactions as (
    select v.store_id, 
    v.date, 
    cast(avg(v.nb_transactions) AS int) as nb_transactions,
    cast(avg(v.chiffre_affaires) AS decimal(10,2)) as chiffre_affaires
    from clean_transactions v
    group by v.store_id, v.date
    )
    
    select v.*, mt.nb_transactions, mt.chiffre_affaires
    from transactions_manquants v
    inner join moyenne_transactions mt
    on v.store_id = mt.store_id
    and v.date = mt.date
""")
transactions_manquants.createOrReplaceTempView("transactions_manquants")
display(transactions_manquants)

store_id date heure nb_transactions chiffre_affaires 5 2023-05-02 16 57 3664.82 8 2023-05-05 12 57 3753.53 10 2023-05-09 15 36 2403.27 4 2023-05-05 14 88 5702.91 7 2023-05-09 16 73 4791.31 1 2023-04-28 16 159 10307.53 8 2023-05-08 13 44 3008.23 2 2023-05-11 16 88 5699.04 2 2023-05-11 17 88 5699.04 6 2023-05-02 11 54 3538.69 3 2023-05-03 17 114 7304.04 7 2023-05-11 16 70 4633.14 5 2023-05-05 18 71 4695.18 3 2023-05-04 19 102 6673.36 9 2023-05-08 10 44 2822.33 1 2023-05-02 19 113 7217.35 6 2023-05-04 10 51 3421.39 10 2023-05-15 17 30 1928.16 2 2023-05-16 9 103 6796.30 10 2023-05-15 10 30 1928.16 3 2023-05-05 16 131 8438.62 4 2023-05-11 14 81 5299.21 4 2023-05-12 15 106 6953.76 7 2023-05-16 14 77 5068.84 1 2023-05-08 19 99 6406.94 3 2023-05-11 11 93 5932.67 7 2023-05-18 17 67 4405.90 1 2023-05-09 14 121 7969.42 10 2023-05-19 11 36 2408.20 4 2023-05-16 9 79 5313.32 2 2023-05-22 13 67 4462.58 9 2023-05-16 13 54 3621.15 1 2023-05-10 10 170 11047.26 8 2023-05-18 9 52 3449.80 9 2023-05-16 12 54 3621.15 3 2023-05-15 14 79 5162.90 10 2023-05-23 10 34 2288.75 7 2023-05-22 10 59 3854.10 9 2023-05-17 9 73 4843.44 2 2023-05-25 9 103 6691.37 9 2023-05-18 17 55 3594.09 9 2023-05-18 12 55 3594.09 6 2023-05-16 10 50 3393.22 6 2023-05-16 11 50 3393.22 7 2023-05-24 18 79 5075.50 2 2023-05-26 11 115 7508.93 4 2023-05-22 13 57 3700.06 4 2023-05-23 14 83 5440.85 9 2023-05-22 15 49 3230.21 7 2023-05-25 19 70 4587.90 3 2023-05-18 19 105 6679.56 7 2023-05-25 15 70 4587.90 3 2023-05-19 13 107 7108.02 5 2023-05-22 14 43 2758.74 3 2023-05-19 17 107 7108.02 10 2023-05-30 18 36 2252.64 8 2023-05-26 18 67 4379.13 10 2023-05-30 11 36 2252.64 2 2023-05-31 12 112 7236.44 1 2023-05-18 17 109 7144.33 3 2023-05-23 17 89 5701.52 7 2023-05-30 13 74 4888.74 9 2023-05-26 18 58 3792.41 8 2023-05-30 9 63 4065.84 3 2023-05-25 13 93 5972.00 4 2023-05-30 18 65 4297.64 4 2023-05-30 19 65 4297.64 6 2023-05-24 16 67 4412.27 7 2023-06-01 11 66 4399.36 5 2023-05-26 19 59 3846.27 1 2023-05-23 17 103 6675.06 9 2023-05-29 10 49 3129.50 7 2023-06-01 13 66 4399.36 1 2023-05-24 9 152 9935.63 6 2023-05-25 11 52 3376.91 5 2023-05-29 17 48 3303.13 2 2023-06-06 14 95 6243.36 6 2023-05-26 10 67 4365.79 9 2023-05-31 13 69 4705.70 4 2023-06-01 14 83 5454.76 10 2023-06-06 19 33 2180.32 9 2023-05-31 9 69 4705.70 8 2023-06-05 17 40 2592.74 2 2023-06-08 10 100 6464.36 8 2023-06-05 10 40 2592.74 7 2023-06-06 11 68 4369.53 9 2023-06-01 10 53 3479.90 7 2023-06-07 16 86 5621.05 6 2023-05-30 11 51 3240.97 7 2023-06-07 18 86 5621.05 7 2023-06-07 9 86 5621.05 6 2023-05-30 15 51 3240.97 1 2023-05-29 17 95 6459.39 3 2023-05-31 9 126 7878.19 4 2023-06-05 12 59 3994.15 1 2023-05-30 10 135 8845.42 8 2023-06-07 18 58 3926.79 10 2023-06-09 9 46 3056.97 10 2023-06-09 11 46 3056.97 2 2023-06-12 12 76 5095.07 6 2023-05-31 16 67 4386.46 8 2023-06-07 10 58 3926.79 3 2023-06-01 9 103 6603.97 2 2023-06-12 17 76 5095.07 5 2023-06-05 14 49 3173.54 2 2023-06-13 10 94 6084.50 9 2023-06-06 18 65 4315.47 4 2023-06-07 19 89 5794.98 2 2023-06-13 12 94 6084.50 1 2023-05-31 16 140 9163.00 1 2023-05-31 18 140 9163.00 1 2023-06-01 14 145 9559.06 6 2023-06-02 16 63 4140.15 5 2023-06-06 10 63 4157.10 10 2023-06-13 15 34 2184.60 8 2023-06-12 9 42 2720.51 1 2023-06-02 16 135 9001.82 10 2023-06-14 16 43 2930.97 5 2023-06-08 16 53 3589.84 2 2023-06-16 11 101 6769.02 8 2023-06-14 16 60 3779.99 9 2023-06-12 15 55 3585.22 1 2023-06-06 14 133 8784.58 6 2023-06-08 11 47 3138.60 9 2023-06-13 14 62 4084.49 4 2023-06-14 18 84 5284.99 9 2023-06-13 18 62 4084.49 8 2023-06-15 11 49 3236.59 8 2023-06-15 13 49 3236.59 1 2023-06-08 13 131 8395.84 6 2023-06-09 17 55 3687.34 7 2023-06-19 14 58 3896.56 5 2023-06-14 15 76 5099.45 10 2023-06-21 11 40 2670.12 1 2023-06-09 15 163 10748.84 2 2023-06-22 13 84 5483.04 9 2023-06-15 9 59 3821.39 6 2023-06-12 18 38 2489.19 6 2023-06-13 10 50 3160.90 2 2023-06-23 18 98 6449.56 8 2023-06-20 17 49 3181.58 7 2023-06-21 10 79 5159.55 6 2023-06-13 16 50 3160.90 2 2023-06-23 16 98 6449.56 4 2023-06-19 13 61 4071.39 

In [0]:
clean_transactions = spark.sql("""
    SELECT store_id, date, heure, nb_transactions, chiffre_affaires
    FROM clean_transactions

    UNION ALL

    SELECT store_id, date, heure, nb_transactions, chiffre_affaires
    FROM transactions_manquants
""")
display(transactions_manquants)


store_id date heure nb_transactions chiffre_affaires 1 2023-08-29 15 127 8308.70 2 2023-09-21 18 83 5518.61 2 2023-10-23 12 68 4508.68 1 2024-01-03 11 156 10224.53 5 2024-01-09 9 67 4421.29 10 2024-08-13 15 37 2380.83 7 2025-01-29 15 90 5932.37 7 2025-03-18 15 67 4336.20 5 2025-03-14 15 72 4708.29 10 2023-08-25 10 40 2594.95 8 2023-11-08 12 58 3860.47 7 2024-01-08 18 61 4045.70 4 2024-02-05 19 60 3896.99 1 2024-02-02 13 148 9630.37 3 2024-04-17 10 123 8113.49 9 2024-08-06 19 65 4306.71 8 2024-11-04 18 40 2528.98 2 2023-06-23 18 98 6449.56 9 2023-10-06 11 76 4968.39 8 2024-04-16 13 47 3225.34 6 2024-07-30 12 51 3242.02 7 2024-08-12 9 64 4029.01 5 2024-11-08 12 72 4702.53 10 2024-11-25 9 28 1884.24 1 2025-03-28 14 167 10968.63 4 2023-08-10 15 78 5090.40 5 2024-01-25 17 65 4221.49 4 2024-03-29 11 85 5499.25 1 2024-05-10 14 128 8266.99 3 2024-07-24 13 106 6903.90 7 2024-09-30 17 56 3653.50 8 2024-11-01 17 60 3946.22 1 2024-11-22 12 132 8437.32 8 2024-12-11 18 57 3651.69 6 2023-06-08 11 47 3138.60 10 2023-11-20 13 24 1508.79 6 2024-02-08 12 47 3053.33 4 2024-03-22 17 87 5524.75 2 2024-05-27 13 72 4629.74 8 2024-07-16 13 52 3307.84 9 2024-10-15 12 63 4126.87 1 2024-11-05 18 127 8152.37 5 2024-12-24 15 56 3769.36 2 2025-03-11 16 98 6404.26 7 2025-04-25 11 89 5633.67 5 2023-05-05 18 71 4695.18 9 2023-05-31 13 69 4705.70 2 2023-08-15 10 96 6329.35 4 2023-09-01 14 83 5502.42 2 2023-10-17 19 99 6440.39 10 2023-10-20 19 46 3052.65 10 2023-12-20 12 40 2550.86 1 2024-03-11 13 89 5840.44 6 2024-05-03 19 52 3408.54 1 2024-06-19 16 151 9861.50 3 2024-09-13 18 123 8247.77 8 2024-10-25 10 64 4120.93 1 2024-12-19 15 135 8956.81 8 2025-03-03 16 46 2972.21 1 2025-03-19 15 160 10534.22 5 2023-08-18 12 69 4540.23 3 2023-09-25 18 67 4367.07 1 2023-10-31 18 112 7357.52 5 2024-01-25 12 65 4221.49 8 2024-04-03 15 56 3702.54 3 2024-04-19 15 116 7744.51 3 2024-04-19 16 116 7744.51 1 2024-07-11 9 141 9138.90 5 2024-08-27 18 53 3549.61 6 2024-09-25 16 66 4466.25 5 2024-11-14 13 51 3313.69 10 2025-01-30 15 38 2573.94 9 2025-04-04 9 79 5083.72 10 2023-08-22 10 38 2399.29 8 2023-11-24 13 54 3465.50 8 2024-01-10 13 56 3785.99 5 2024-06-20 14 57 3655.92 1 2024-07-18 12 126 8412.39 4 2024-08-06 14 80 5341.37 1 2024-08-02 17 173 11354.89 6 2024-12-27 15 63 4215.21 8 2025-02-03 9 47 3032.07 1 2025-04-14 11 97 6315.33 3 2023-05-04 19 102 6673.36 6 2023-05-04 10 51 3421.39 8 2023-05-26 18 67 4379.13 1 2023-06-01 14 145 9559.06 10 2023-10-11 9 44 2797.60 1 2023-12-14 18 140 9051.31 6 2024-02-21 17 54 3539.77 9 2024-04-03 10 71 4603.36 4 2024-08-13 15 73 4914.78 3 2024-08-22 16 89 5829.25 4 2024-10-02 17 85 5579.66 10 2024-12-23 9 29 2002.76 1 2025-03-24 12 104 6722.31 10 2024-03-01 13 40 2632.25 4 2024-05-22 18 93 5777.53 5 2024-07-24 18 74 4874.34 10 2024-10-17 17 35 2469.30 1 2024-11-14 14 120 7900.48 6 2025-02-27 15 53 3374.88 5 2025-03-04 11 64 4192.40 5 2025-03-20 18 57 3636.66 9 2023-05-08 10 44 2822.33 9 2023-05-16 13 54 3621.15 10 2023-06-21 11 40 2670.12 4 2023-06-21 9 88 5505.03 8 2023-06-27 12 53 3507.28 5 2023-07-18 13 57 3689.40 5 2023-07-24 17 39 2715.60 5 2023-08-07 18 38 2518.82 10 2023-08-16 16 45 2953.51 1 2024-02-08 19 129 8330.80 2 2024-03-21 18 87 5802.89 10 2024-03-29 17 39 2605.86 8 2024-06-27 17 49 3206.93 7 2024-11-28 18 65 4302.52 3 2024-12-26 19 92 5868.21 9 2025-02-26 12 72 4673.99 10 2025-03-13 15 34 2156.45 10 2023-06-28 17 41 2700.35 8 2023-06-28 16 54 3473.28 3 2023-08-11 13 97 6502.22 7 2023-08-18 19 86 5638.95 10 2023-08-24 19 35 2377.61 8 2024-01-02 11 50 3300.66 5 2024-02-02 15 70 4543.05 8 2024-05-13 11 41 2695.15 3 2024-06-20 15 92 5902.35 7 2023-07-21 18 87 5681.22 5 2023-08-30 12 83 5577.25 8 2023-09-21 9 55 3714.21 8 2023-09-25 11 40 2543.52 4 2023-10-04 18 96 6243.66 3 2024-01-25 13 109 7114.48 10 2024-02-06 17 31 1956.75 7 2024-05-27 15 57 3744.63 3 2024-05-27 18 85 5502.36 2 2024-06-12 17 99 6542.19 7 2024-06-14 16 76 5130.84 6 2024-09-16 12 37 2544.07 9 2025-01-22 16 78 5194.98 7 2023-06-06 11 68 4369.53 7 2023-09-11 13 63 4

In [0]:
clean_transactions.groupBy("date", "heure", "store_id") \
    .agg(F.count("*").alias("nb")) \
    .filter(F.col("nb") > 1) \
    .show()

+----+-----+--------+---+
|date|heure|store_id| nb|
+----+-----+--------+---+
+----+-----+--------+---+



In [0]:
clean_transactions.count()

57420

In [0]:
clean_transactions = clean_transactions.dropDuplicates(
    ["date", "heure", "store_id"]
)

In [0]:
clean_transactions.count()

57420

In [0]:
clean_transactions.select(F.min(F.col("date")), F.max(F.col("date"))).show()

+----------+----------+
| min(date)| max(date)|
+----------+----------+
|2023-04-27|2025-04-25|
+----------+----------+



In [0]:
try:
    clean_transactions.write.jdbc(
        url=jdbcUrl,
        table="analytics.transactions",
        mode="append",  # ou "overwrite" selon usage
        properties=connectionProperties
    )
    print("Données insérées avec succès dans analytics.transactions.")
except Exception as e:
    print("Erreur lors de l'insertion dans la base SQL :")
    print(str(e))